## Intraday vwap mean reverting

Desription: mean reverting intraday strategy with momentum entry

Goal is to recreate strategy in vectorbptro and compare with v2trading engine backtest.

Symbol: BAC
Timeframe: 12s
Backtested on: 1s
Entry window: 0 - 380 (mins. from open)
EOD Exit: 382-390

Indicators:
- vwap_cum - Anchored daily cumulative vwap 
- div_vwap_cum - Divergence of vwap_cum and close 
- div_vwap_angle - Linreg angle of div_vwap_cum over period N (hp1)

**Long entries:**
- div_vwap_angle.AND.go_short_if_fallingc = 3 (hp2)
- div_vwap_cum.AND.go_short_if_above = 0 (hp3)

**Short entries:**
- div_vwap_angle.AND.go_long_if_risingc = 3 (hp2)
- div_vwap_cum.AND.go_long_if_below = 0 (hp3)

**Exits:**
only SL, TP pct based
- SL: 0.3 (hp4)
- TP: 0.4 (hp5)

hp - hyperparameters for tuning

In [1]:
import vectorbtpro as vbt
import ttools as tts
from lightweight_charts import chart, Panel, PlotDFAccessor, PlotSRAccessor
import talib
from numba import jit
import pandas as pd
import numpy as np


In [2]:
 #fetching from remote db
from lib.db import Connection
SYMBOL = "BAC"
SCHEMA = "ohlcv_1s" #time based 1s other options ohlcv_vol_200 (volume based ohlcv with resolution of 200), ohlcv_renko_20 (renko with 20 bricks size) ...
DB = "market_data"

con = Connection(db_name=DB, default_schema=SCHEMA, create_db=True)
basic_data = con.pull(symbols=[SYMBOL], schema=SCHEMA,start="2024-10-14", end="2024-10-17", tz_convert='America/New_York')

#basic_data = basic_data.add_symbol("BAC2", basic_data.data["BAC"])

#basic_data.index.normalize().nunique()

100%|##########| 1/1 [00:09<00:00,  9.19s/it, symbol=BAC]

In [3]:
basic_data = basic_data[['open',
 'high',
 'low',
 'close',
 'volume']]

In [4]:
#Resample to 12s
s12_data = basic_data.resample("12s")
s12_data = s12_data.transform(lambda df: df.between_time('09:30', '16:00').dropna())

s12_data.data["BAC"].lw.plot()

In [5]:
#s12_data = s12_data.add_symbol("BAC3", s12_data.data["BAC"])
s12_data.symbols

['BAC']

In [6]:
s12_data = s12_data.add_symbol("BAC-SHORT", s12_data.data["BAC-LONG"])

KeyError: 'BAC-LONG'

In [46]:
vbt.IF.list_indicators("*DIV*")

['ttools:DIVRELN', 'talib:DIV']

In [37]:
vbt.phelp(vbt.indicator("talib:LINEARREG_ANGLE").run)

LINEARREG_ANGLE.run(
    close,
    timeperiod=Default(value=14),
    timeframe=Default(value=None),
    short_name='linearreg_angle',
    hide_params=None,
    hide_default=True,
    **kwargs
):
    Run `LINEARREG_ANGLE` indicator.
    
    * Inputs: `close`
    * Parameters: `timeperiod`, `timeframe`
    * Outputs: `real`
    
    Pass a list of parameter names as `hide_params` to hide their column levels, or True to hide all.
    Set `hide_default` to False to show the column levels of the parameters with a default value.
    
    Other keyword arguments are passed to `LINEARREG_ANGLE.run_pipeline`.


In [55]:
from numba import jit
import numpy as np

@jit(nopython=True)
def isrisingc(pole: np.ndarray, pocet: int) -> np.ndarray:
    # Ensure pocet is valid
    if pocet < 1 or pocet > pole.shape[0]:
        raise ValueError("Invalid window size.")

    # Create a result array initialized to False
    result = np.zeros(pole.shape[0], dtype=np.bool_)

    # Iterate through the array, starting from the first valid rolling window
    for i in range(pocet - 1, pole.shape[0]):
        is_increasing = True
        # Compare the current value with the previous value within the rolling window
        for j in range(i - pocet + 2, i + 1):  # Start comparison from the second element in the window
            if pole[j] <= pole[j - 1]:  # Check if current element is not greater than the previous one
                is_increasing = False
                break
        result[i] = is_increasing

    return result


In [119]:
#s12_data.ohlcv.data["BAC"].vbt.xloc[slice("2024-10-14 15:50:00", "2024-10-15 15:50:00")].obj.head(10)

a = div_vwap_cum.xloc[slice("2024-10-14 15:50:00", "2024-10-15 15:50:00")].div.head(60)
a

symbol                        BAC
time                             
2024-10-14 15:50:00-04:00 -0.0000
2024-10-14 15:50:12-04:00 -0.0000
2024-10-14 15:50:24-04:00 -0.0000
2024-10-14 15:50:36-04:00 -0.0000
2024-10-14 15:50:48-04:00 -0.0000
2024-10-14 15:51:00-04:00 -0.0000
2024-10-14 15:51:12-04:00 -0.0002
2024-10-14 15:51:24-04:00 -0.0002
2024-10-14 15:51:36-04:00 -0.0002
2024-10-14 15:51:48-04:00 -0.0002
2024-10-14 15:52:00-04:00  0.0000
2024-10-14 15:52:12-04:00  0.0000
2024-10-14 15:52:24-04:00  0.0002
2024-10-14 15:52:36-04:00  0.0001
2024-10-14 15:52:48-04:00  0.0001
2024-10-14 15:53:00-04:00 -0.0001
2024-10-14 15:53:12-04:00 -0.0000
2024-10-14 15:53:24-04:00  0.0000
2024-10-14 15:53:36-04:00  0.0001
2024-10-14 15:53:48-04:00  0.0002
2024-10-14 15:54:00-04:00  0.0004
2024-10-14 15:54:12-04:00  0.0004
2024-10-14 15:54:24-04:00  0.0005
2024-10-14 15:54:36-04:00  0.0004
2024-10-14 15:54:48-04:00  0.0004
2024-10-14 15:55:00-04:00  0.0005
2024-10-14 15:55:12-04:00  0.0005
2024-10-14 15:55:24-04:00  0.0007
2024-10-14 15:55:36-04:00  0.0008
2024-10-14 15:55:48-04:00  0.0005
2024-10-14 15:56:00-04:00  0.0006
2024-10-14 15:56:12-04:00  0.0004
2024-10-14 15:56:24-04:00  0.0003
2024-10-14 15:56:36-04:00  0.0003
2024-10-14 15:56:48-04:00  0.0005
2024-10-14 15:57:00-04:00  0.0005
2024-10-14 15:57:12-04:00  0.0004
2024-10-14 15:57:24-04:00  0.0002
2024-10-14 15:57:36-04:00  0.0003
2024-10-14 15:57:48-04:00  0.0004
2024-10-14 15:58:00-04:00  0.0004
2024-10-14 15:58:12-04:00  0.0004
2024-10-14 15:58:24-04:00  0.0003
2024-10-14 15:58:36-04:00  0.0003
2024-10-14 15:58:48-04:00  0.0001
2024-10-14 15:59:00-04:00  0.0002
2024-10-14 15:59:12-04:00  0.0003
2024-10-14 15:59:24-04:00 -0.0003
2024-10-14 15:59:36-04:00 -0.0002
2024-10-14 15:59:48-04:00 -0.0001
2024-10-15 09:30:00-04:00  0.0101
2024-10-15 09:30:12-04:00  0.0090
2024-10-15 09:30:24-04:00  0.0095
2024-10-15 09:30:36-04:00  0.0095
2024-10-15 09:30:48-04:00  0.0077
2024-10-15 09:31:00-04:00  0.0075
2024-10-15 09:31:12-04:00  0.0063
2024-10-15 09:31:24-04:00  0.0067
2024-10-15 09:31:36-04:00  0.0060
2024-10-15 09:31:48-04:00  0.0047

In [12]:
%load_ext autoreload
%autoreload 2
from ttools.vbtindicators import register_custom_inds
register_custom_inds(None, "override")
#chopiness = vbt.indicator("technical:CHOPINESS").run(s12_data.open, s12_data.high, s12_data.low, s12_data.close, s12_data.volume, window = 100)
#vwap_cum_roll = vbt.indicator("technical:ROLLING_VWAP").run(s12_data.open, s12_data.high, s12_data.low, s12_data.close, s12_data.volume, window = 100, min_periods = 5)

#note that VWAP is calculated from HLCC4 rounded to 3 decimals, can be changed by hlcc4_round parameter
vwap_cum_d = vbt.indicator("ttools:CUVWAP").run(s12_data.high, s12_data.low, s12_data.close, s12_data.volume, anchor=vbt.Default(value="D"), drag=vbt.Default(value=50), hide_default=True)
div_vwap_cum = vbt.indicator("ttools:DIVERGENCE").run(s12_data.close, vwap_cum_d.vwap, divtype=vbt.Default(value="reln"), hide_default=True)
div_vwap_lin_angle = vbt.indicator("talib:LINEARREG_ANGLE").run(div_vwap_cum.div, timeperiod=2)
dvla = np.round(div_vwap_lin_angle.real,4)

long_entries = tts.isrisingc(dvla,3).vbt & div_vwap_cum.div_below(0)
short_entries = tts.isfallingc(dvla,3).vbt & div_vwap_cum.div_above(0)

#SIGNAL - make indicator with 1 - long, -1 - short, 0 nothing
long_series = long_entries.squeeze()
short_series = short_entries.squeeze()
signals = pd.Series(0, index=long_series.index)  # Initialize with 0
signals[long_series] = 1  # Set 1 where entries are True
signals[short_series] = -1   # Set -1 where exits are True

Panel(
    ohlcv=(s12_data.ohlcv.data["BAC"],), #[(long_entries.squeeze())],[(short_entries.squeeze())]),
    right=[(vwap_cum_d.vwap, "vwap_cum_daily")], 
    middle1=[(div_vwap_lin_angle.real, "div_vwap_angle")],
    middle2=[(signals, "signals")],
    left=[(div_vwap_cum.div, "div_vwap_cum")]).chart(size="m", xloc=slice("2024-10-14 15:00:00", "2024-10-15 16:00:00"), precision=4)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [ ]:
#TED backtest, porovnat s v2realbot, delsi obdobi, tuning parametru a zpetne vyzkouseni s realbotem
#pripadne mrknout na markov variance switching zda nepujde na intraday

In [40]:
from typing import Any
from ttools import create_mask_from_window

#single for exits, as it is just EOD exits
exits = pd.DataFrame.vbt.signals.empty_like(long_entries) 
entry_window_opens = 0 #in minutes from start of the market
entry_window_closes = 380
forced_exit_start = 382
forced_exit_end = 390

#create mask based on main session that day
entry_window_opened = create_mask_from_window(long_entries, entry_window_opens, entry_window_closes, use_cal=False)
#limit entries to the window
long_entries_cln = long_entries.vbt & entry_window_opened
short_entries_cln = short_entries.vbt & entry_window_opened

#create forced exits mask
forced_exits_window = create_mask_from_window(exits, forced_exit_start, forced_exit_end, use_cal=False)

#add just forced EOD exits to exits, series is ok
long_exits = forced_exits_window
short_exits = forced_exits_window

In [38]:
long_exits


linearreg_angle_timeperiod      2
symbol                        BAC
time                             
2024-10-03 09:30:00-04:00   False
2024-10-03 09:30:12-04:00   False
2024-10-03 09:30:24-04:00   False
2024-10-03 09:30:36-04:00   False
2024-10-03 09:30:48-04:00   False
...                           ...
2024-10-16 15:59:00-04:00   False
2024-10-16 15:59:12-04:00   False
2024-10-16 15:59:24-04:00   False
2024-10-16 15:59:36-04:00   False
2024-10-16 15:59:48-04:00   False

[19393 rows x 1 columns]

In [154]:
s12_data.wrapper.shape[0]

19393

In [155]:
group_lens =s12_data.wrapper.get_index_grouper("D").get_group_lens()

In [157]:
group_end_idxs = np.cumsum(group_lens)
# # group_start_idxs = group_end_idxs - group_lens

array([    0,  1941,  3871,  5799,  7727,  9669, 11601, 13551, 15500,
       17448])

In [144]:
s12_data.ohlcv.data["BAC-LONG"].lw.plot(right=[(vwap_cum, "vwap")])

In [61]:
import talib
pd.set_option('display.max_rows', 500)
def apply_func_1d(close, high, timeperiod):
    return talib.SMA(close.astype(np.double), timeperiod)

SMA = vbt.IF(
    input_names=['close', 'high'],
    param_names=['timeperiod'],
    output_names=['sma']
).with_apply_func(
    apply_func_1d,
    takes_1d=True,
    timeperiod=10, #single default
    high=vbt.Ref('close')) #default from another input

ind = SMA.run(s12_data.close)
ind.sma
#sma.sma

symbol                         BAC
time                              
2024-10-03 09:30:00-04:00      NaN
2024-10-03 09:30:12-04:00      NaN
2024-10-03 09:30:24-04:00      NaN
2024-10-03 09:30:36-04:00      NaN
2024-10-03 09:30:48-04:00      NaN
...                            ...
2024-10-16 15:59:00-04:00  42.7735
2024-10-16 15:59:12-04:00  42.7720
2024-10-16 15:59:24-04:00  42.7715
2024-10-16 15:59:36-04:00  42.7730
2024-10-16 15:59:48-04:00  42.7770

[19393 rows x 1 columns]

In [39]:
#vbt.IF.list_indicators("*vwap")
vbt.phelp(vbt.indicator("technical:ROLLING_VWAP").run)


ROLLING_VWAP.run(
    open,
    high,
    low,
    close,
    volume,
    window=Default(value=200),
    min_periods=Default(value=None),
    short_name='rolling_vwap',
    hide_params=None,
    hide_default=True,
    **kwargs
):
    Run `ROLLING_VWAP` indicator.
    
    * Inputs: `open`, `high`, `low`, `close`, `volume`
    * Parameters: `window`, `min_periods`
    * Outputs: `rolling_vwap`
    
    Pass a list of parameter names as `hide_params` to hide their column levels, or True to hide all.
    Set `hide_default` to False to show the column levels of the parameters with a default value.
    
    Other keyword arguments are passed to `ROLLING_VWAP.run_pipeline`.
